In [1]:
# Dependencies and Setup
import pandas as pd
import numpy as np
import time
from pprint import pprint
import requests
from datetime import date, timedelta, datetime
import json
from pprint import pprint
from tqdm import tqdm
from tqdm import tqdm_notebook
# sqlite Dependencies
# ----------------------------------
# Imports the method used for connecting to DBs
from sqlalchemy import create_engine
# Allow us to declare column types
from sqlalchemy import Column, Integer, String, Text, DateTime, Float, Boolean, ForeignKey
from sqlalchemy.orm import relationship
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy.orm import Session

In [2]:
from nba_api.stats.endpoints import playercareerstats, drafthistory, commonplayerinfo, playerawards

In [3]:
# Not used
# cumestatsplayer,draftcombinedrillresults,playerdashboardbyteamperformance, leagueleaders, leaguedashplayerstats, draftcombinenonstationaryshooting, draftcombinestats, commonallplayers,

-------------

# Open Saved JSON

In [101]:
with open('./_players_all_data.json') as json_file:
    data = json.load(json_file)

In [102]:
#  Player positions
player_positions = pd.read_csv('../../datasets/nba_positions_no_team.csv') 

In [103]:
five_year_all_players = pd.read_json(data)
twenty_years_all_players_raw = five_year_all_players[five_year_all_players['SEASON_ID'] > '1999-00']
twenty_years_all_players_raw = twenty_years_all_players_raw.join(player_positions.set_index('PLAYER_NAME'), on='PLAYER_NAME')
twenty_years_all_players_raw = twenty_years_all_players_raw.dropna(how='any').sort_values(by=['PTS'], ascending=False).drop_duplicates( keep='first').reset_index(drop=True)
twenty_years_all_players_raw['PPGP'] = round(twenty_years_all_players['PTS'] / twenty_years_all_players['GP'], 2)
twenty_years_all_players = twenty_years_all_players_raw.copy()
twenty_years_all_players

PLAYER_ID SEASON_ID  LEAGUE_ID     TEAM_ID TEAM_ABBREVIATION  \
0          2544   2005-06          0  1610612739               CLE   
1        201142   2009-10          0  1610612760               OKC   
2          2240   2005-06          0  1610612764               WAS   
3          2544   2007-08          0  1610612739               CLE   
4           947   2000-01          0  1610612755               PHI   
...         ...       ...        ...         ...               ...   
5322     202918   2017-18          0  1610612738               BOS   
5323     204067   2017-18          0  1610612738               BOS   
5324       2062   2002-03          0  1610612744               GSW   
5325     204067   2017-18          0  1610612741               CHI   
5326     204067   2017-18          0           0               TOT   

      PLAYER_AGE  GP    GS     MIN  FGM  ...  AST    STL   BLK    TOV   PF  \
0             21  79  79.0  3361.0  875  ...  521  123.0  66.0  260.0  181   
1             21  82  82.0  3239.0  794  ...  231  112.0  84.0  271.0  171   
2             24  80  80.0  3384.0  746  ...  484  161.0  25.0  297.0  286   
3             23  75  74.0  3027.0  794  ...  539  138.0  81.0  255.0  165   
4             26  71  71.0  2976.0  762  ...  325  178.0  20.0  237.0  147   
...          ...  ..   ...     ...  ...  ...  ...    ...   ...    ...  ...   
5322          30   2   0.0     8.0    0  ...    0    1.0   0.0    0.0    1   
5323          26   2   0.0     6.0    0  ...    0    1.0   0.0    0.0    0   
5324          25   2   0.0     9.0    0  ...    2    1.0   0.0    1.0    0   
5325          26   1   0.0     3.0    0  ...    0    0.0   0.0    0.0    0   
5326          26   3   0.0     9.0    0  ...    0    1.0   0.0    0.0    0   

       PTS  YIL     PLAYER_NAME  POSITION   PPGP  
0     2478    3    LeBron James        SF  31.37  
1     2472    3    Kevin Durant        SF  30.15  
2     2346    5  Gilbert Arenas        PG  29.32  
3     2250    5    LeBron James        SF  30.00  
4     2207    5   Allen Iverson        SG  31.08  
...    ...  ...             ...       ...    ...  
5322     0    2    Xavier Silas         G   0.00  
5323     0    3    Jarell Eddie         F   0.00  
5324     0    3     A.J. Guyton         G   0.00  
5325     0    3    Jarell Eddie         F   0.00  
5326     0    3    Jarell Eddie         F   0.00  

[5327 rows x 31 columns]

In [104]:
### DF for each year. decending
first_year = twenty_years_all_players[twenty_years_all_players['YIL'] == 1]
second_year = twenty_years_all_players[twenty_years_all_players['YIL'] == 2]
third_year = twenty_years_all_players[twenty_years_all_players['YIL'] == 3]
fourth_year = twenty_years_all_players[twenty_years_all_players['YIL'] == 4]
fifth_year = twenty_years_all_players[twenty_years_all_players['YIL'] == 5]

## Plot YIL to Total Points

First Year Total Points per Position

In [107]:
import plotly.express as px

fig = px.scatter(twenty_years_all_players, x="MIN", y="PPGP", log_x=True, hover_name="PLAYER_NAME", hover_data=["PTS", 'PPGP', 'SEASON_ID', 'TEAM_ABBREVIATION'], color="YIL",
                 size='PTS', title="First Year Total Points per Position")
fig.show()

Second Year Total Points per Position

In [108]:
import plotly.express as px

fig = px.scatter(second_year, x="PTS", y="POSITION", log_x=True, hover_name="PLAYER_NAME", hover_data=["PTS"], color="PTS",
                 size='PTS', title="Second Year Total Points per Position")
fig.show()

In [70]:
## Remove NaN . Will sway values greatly
# first_year = first_year.dropna().sort_values(by=['PTS'], ascending=False).drop_duplicates( keep='first')
# first_year

In [71]:
test = list(first_year.columns.values)

In [72]:
fig = px.scatter_polar(first_year, r="PTS", theta="POSITION", color="PTS",
                    template="plotly_dark", title="First Year Total Points per Position")
fig.show()

In [73]:
twenty_years_all_players[['YIL','PTS','STL','BLK','REB','MIN','AST','TOV']].columns

Index(['YIL', 'PTS', 'STL', 'BLK', 'REB', 'MIN', 'AST', 'TOV'], dtype='object')

In [76]:
import plotly.express as px
df = px.data.stocks()
fig = px.line(twenty_years_all_players, x="MIN", y=twenty_years_all_players[['YIL','PTS','STL','BLK','REB','MIN','AST','TOV']].columns,
              hover_data={"PLAYER_NAME"},
              title='custom tick labels',
             color="YIL")
# fig.update_xaxes(
#     dtick="M1",
#     tickformat="%b\n%Y")
fig.show()

https://plotly.com/python/polar-chart/

In [25]:
# import plotly.express as px
# df = px.data.wind()
# fig = px.line_polar(twenty_years_all_players, r="PTS", theta="POSITION", color="YIL", line_close=True,
#                     color_discrete_sequence=px.colors.sequential.Plasma_r,
#                     template="plotly_dark",)
# fig.show()

In [26]:
# df = px.data.wind()
# df